In [8]:
from bs4 import  BeautifulSoup
from selenium.webdriver.common.by import By
from urllib.request import urlopen
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from selenium import webdriver
import time
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import Select
from time import sleep
from selenium.webdriver import ActionChains
import pickle
import json
import requests
import sqlite3

client_id = "l5s8tg1g0w" # 개발자센터에서 발급받은 Client ID 값
client_secret = "RPNXQKCp8erMRW4KvKWsME5m3F9QOYVJTZ8Lvj56" # 개발자센터에서 발급받은 Client Secret 값

user_agent = 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/60.0.3112.50 Safari/537.36'

options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')
options.add_argument('user-agent={0}'.format(user_agent))
# options =  webdriver.Chrome('/home/porter/NOTEBOOK/chromedriver',options=options)
conn = sqlite3.connect("/home/lsi8505/miraeasset/crawling/opinion_outside.db")
cur = conn.cursor()

client_id = "l5s8tg1g0w" # 개발자센터에서 발급받은 Client ID 값
client_secret = "RPNXQKCp8erMRW4KvKWsME5m3F9QOYVJTZ8Lvj56" # 개발자센터에서 발급받은 Client Secret 값

def get_sentiment(content):
    printout = True
    url="https://naveropenapi.apigw.ntruss.com/sentiment-analysis/v1/analyze"

    headers = {
        "X-NCP-APIGW-API-KEY-ID": client_id,
        "X-NCP-APIGW-API-KEY": client_secret,
        "Content-Type": "application/json"
    }

    data = {
      "content": content
    }

    response = requests.post(url, data=json.dumps(data), headers=headers)
    rescode = response.status_code

    if(rescode == 200):        
        sentiment = json.loads(response.text)['document']['sentiment'] 
        pos_score = json.loads(response.text)['document']['confidence']['positive']
        neg_score = json.loads(response.text)['document']['confidence']['negative']
        neu_score = json.loads(response.text)['document']['confidence']['neutral']
#         if printout:
#             print("\n=== 감성분석 ===")
#             print("판정: {}\n점수: 긍정 {}, 중립 {}, 부정 {}".format(sentiment, pos_score, neu_score, neg_score)) 
#         return sentiment, pos_score, neu_score, neg_score
        return pos_score

    else:
        print("Error : " + response.text)
        return np.nan     
    

In [3]:
driver = webdriver.Chrome('/home/lsi8505/chromedriver',options=options)
#target of crawling
data_list = []
driver.get("https://www.youtube.com/c/SmartMoney0/videos")
time.sleep(10)
html= driver.page_source
html_res = BeautifulSoup(html, "html.parser") 
videos_l = []
for vid in range(len(html_res.find_all("ytd-grid-video-renderer"))):
    if "days ago" in html_res.find_all("ytd-grid-video-renderer")[vid].find_all("span", {"class": "style-scope ytd-grid-video-renderer"})[1].text:
        sub_url = html_res.find_all("ytd-grid-video-renderer")[vid].find_all("a", {"class": "yt-simple-endpoint style-scope ytd-grid-video-renderer"})[0]['href']
        videos_l.append("https://www.youtube.com{}".format( sub_url))
videos_l

driver.quit()

['https://www.youtube.com/watch?v=aEMSAMKTQdM',
 'https://www.youtube.com/watch?v=YwCE0H07UbI',
 'https://www.youtube.com/watch?v=lEJcJ1JZb28',
 'https://www.youtube.com/watch?v=TK3qnz2fkNQ',
 'https://www.youtube.com/shorts/qK55DdVlV0M',
 'https://www.youtube.com/watch?v=g1NmmEDcPL4',
 'https://www.youtube.com/watch?v=I6vhgsQKwHA',
 'https://www.youtube.com/watch?v=Q-wvA67ATdw',
 'https://www.youtube.com/shorts/NEujoPurOes',
 'https://www.youtube.com/watch?v=G8VMSxQAUio',
 'https://www.youtube.com/watch?v=Eclr61ZbMFc',
 'https://www.youtube.com/watch?v=BKUEZFjiwz0',
 'https://www.youtube.com/watch?v=e8Bx62xoUx4',
 'https://www.youtube.com/watch?v=hI3DrYHACoA',
 'https://www.youtube.com/watch?v=w0PDDRwvA54',
 'https://www.youtube.com/watch?v=6RFqvYy-87Y',
 'https://www.youtube.com/watch?v=GqBVILqwFPc',
 'https://www.youtube.com/watch?v=nJUc_u-wf00',
 'https://www.youtube.com/watch?v=s05La9Jy-qU',
 'https://www.youtube.com/watch?v=cjoo82DDgT0',
 'https://www.youtube.com/watch?v=cvmVz94_

In [5]:
driver = webdriver.Chrome('/home/lsi8505/chromedriver',options=options)

In [6]:
for i in range(len(videos_l)):
    driver.get(videos_l[i])
    time.sleep(10)
    break

In [18]:
videos_l[-3]

'https://www.youtube.com/watch?v=cjoo82DDgT0'

In [20]:
driver.get(videos_l[-3])
time.sleep(10)
html_source = driver.page_source
soup = BeautifulSoup(html_source, 'html.parser')

id_list = soup.select("div#header-author > h3 > #author-text > span")
comment_list = soup.select("yt-formatted-string#content-text")

id_final = []
comment_final = []

for i in range(len(comment_list)):
    temp_id = id_list[i].text
    temp_id = temp_id.replace('\n', '')
    temp_id = temp_id.replace('\t', '')
    temp_id = temp_id.replace('    ', '')
    id_final.append(temp_id) # 댓글 작성자

    temp_comment = comment_list[i].text
    temp_comment = temp_comment.replace('\n', '')
    temp_comment = temp_comment.replace('\t', '')
    temp_comment = temp_comment.replace('    ', '')
    comment_final.append(temp_comment) # 댓글 내용
    
df_ = pd.DataFrame()
df_['DATETIME'] =(datetime.now() - timedelta(hours=15)).strftime('%Y%m%d-%H%M%S')
df_['VIEWS'] = np.nan
df_['LIKES'] = np.nan
df_['TITLE'] =  comment_final
df_['CONTENT'] = np.nan
df_['WRITER'] = id_final

df_['SOURCE'] = "Youtube_스마트머니"
df_['RELATED_ITEM'] = np.nan
df_['POSITIVITY'] = np.nan
for i in range(len(df_)):
    df_.loc[i,"POSITIVITY"] = get_sentiment(df_.loc[i,"TITLE"])

df_['OTHERS'] = df_[['WRITER']].to_dict('records')
df_['OTHERS'] = df_['OTHERS'].astype(str)
df_['NUM_REPLY'] =np.nan
df_['CRAWLING_DATETIME'] = (datetime.now() + timedelta(hours=9)).strftime('%Y%m%d-%H%M%S')
df_['URL'] =  videos_l[i]
df_


MaxRetryError: HTTPConnectionPool(host='127.0.0.1', port=55077): Max retries exceeded with url: /session/920455df65cffe9c75118249f63c48ef/url (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7faf9bbdefa0>: Failed to establish a new connection: [Errno 111] Connection refused'))

In [13]:
 soup.select("yt-formatted-string#content-text")

[]

In [16]:
soup

<html lang="en" style="font-size: 10px;font-family: Roboto, Arial, sans-serif;" system-icons="" typography="" typography-spacing=""><head><script class="js-httpswwwyoutubecomsplayerc57c113cplayer_iasvflseten_USannotations_modulejs" data-original-src="/s/player/c57c113c/player_ias.vflset/en_US/annotations_module.js" nonce="uW8JVzlIuLRGQeVf5-RPwQ" src="/s/player/c57c113c/player_ias.vflset/en_US/annotations_module.js"></script><script class="js-httpswwwyoutubecomsplayerc57c113cplayer_iasvflseten_USendscreenjs" data-original-src="/s/player/c57c113c/player_ias.vflset/en_US/endscreen.js" nonce="uW8JVzlIuLRGQeVf5-RPwQ" src="/s/player/c57c113c/player_ias.vflset/en_US/endscreen.js"></script><script class="js-httpswwwyoutubecomsplayerc57c113cplayer_iasvflseten_UScaptionsjs" data-original-src="/s/player/c57c113c/player_ias.vflset/en_US/captions.js" nonce="uW8JVzlIuLRGQeVf5-RPwQ" src="/s/player/c57c113c/player_ias.vflset/en_US/captions.js"></script><script class="js-httpswwwyoutubecomsplayerc57c11

In [15]:
comments_list

NameError: name 'comments_list' is not defined